# Workshop: numpy/scipy

### Monday, March 6, 2022

In today's workshop we'll get a bit of practice using `numpy` and `scipy`. These two related packages are by far the most commonly used tools in Python for scientific computing (for, e.g., working with matrices, statistical tests and distributions, optimization, etc.).

Given their breadth, we will only scratch the surface in this course, but these two packages are well worth your time if you expect to do any serious amount of numerical computing in Python.

The block of code below imports both packages and gives them convenient names.
If this code does not run successfully, you'll need to install `numpy` and `scipy`.

<b>numpy:<b> https://numpy.org/install/

<b>SciPy:</b> https://scipy.org/install/

In [ ]:
import numpy as np
import scipy as sp

## Problem 1: basics of numpy arrays 

The basic object in `numpy` is the array, which roughly corresponds to a vector, and supports mostly the same operations as do Python lists. Indeed, the easiest way to create a numpy array is to start with a list.

In [ ]:
t = [0,1,4,9,16,25]
a = np.array( t )
a

Create a numpy array `b` that contains the first 10 cubes, starting with 0. You may find it easiest to write a list comprehension and then cast that list to a numpy array.

In [ ]:
# TODO: code goes here.

Adding numpy arrays is possible in the natural way, if we think of them as vectors. Addition is entrywise.

In [ ]:
a = np.array([1,2,3,4])
b = np.array([4,3,2,1])
a+b

We just added two numpy arrays of the same length, and the behavior was as expected if `a` and `b` represented vectors.
Let's try adding two arrays of different lengths.
Specifically, let's try adding a scalar to an array.

In [ ]:
a = np.array([[1,2,3,4]])
a + 1

In regular old vector land, writing something like $v + 1$ doesn't make sense.
But in numpy, this is perfectly fine-- numpy finds a way to "vectorize" the operation along the whole vector (very strictly speaking, what is happening here is actually more related to broadcasting, which is discussed in lecture, but they're close enough...).

Indeed, this kind of idea extends a lot further: many operations in numpy can be <i>vectorized</i>.
We can take a function that applies to scalars, and apply it to every entry of a numpy array.

As an example, consider the following code:

In [ ]:
a = np.array([1,2,3,4])
a**2

If we try to square a plain old Python list in this same way, we get an error-- Python doesn't know how to square lists, only numeric data.

In [ ]:
t = [1,2,3,4]
t**2

Using the above, write a function `my_euc_norm` that takes a single numpy array as its only argument and computes its norm (you may assume this array has shape `(1,p)` for some `p`).

Recall that the Euclidean norm is given by $\| v \| = \sqrt{ \sum_i v_i^2 }$.

<b>Hint:</b> `np.sqrt` and `np.sum` are your friends, here.

In [ ]:
np.sqrt( 10 )

In [ ]:
np.sum( np.array([1,2,3,4,5]) )

In [ ]:
def my_euc_norm( v ):
    # Assuming that v is a one-dimensional numpy array,
    # something like v = np.array( [1,2,3,...,n ]).
    pass # TODO: erase the pass statement and write code here.

In [ ]:
my_euc_norm( np.array([1,1,1])) # Should evaluate to sqrt(3) = 1.732...

In [ ]:
my_euc_norm( np.array([1,0,0,0,0,0])) # Should evaluate to 1.0

## Problem 2: the advantage of ufuncs

So, why do we care about all this broadcasting and vectorization business?

Well, let's try an experiment. Above, we wrote a function for computing the Euclidean norm using vectorized operations.

Here's another function that does the same thing, but using "native Python" for-loops.

In [ ]:
def my_euc_norm_slow( v ):
    res = 0.0
    for i in range(len(v)):
        res += v[i]**2
    # We're using the numpy sqrt function, so we can be confident that any differences in
    # the speed of this function and the speed of my_euc_norm are due to the for-loop--
    # both functions use np.sqrt!
    return np.sqrt(res)

Write a function called `eucnorm_time_trial` that takes a single argument `n` (a positive integer), generates a random numpy array of length `n`, and then uses the Python `time` module to time how long `my_euc_norm` and `my_euc_norm_slow` take to compute the Euclidean norm of this random numpy array.
Your function should then print the results of the experiment in a format like (you are free to vary this as you see fit-- the precise format isn't important, here):

`native Python : X seconds.`

`vectorized : Y seconds.`

<b>Hint:</b> `np.random.random(k)` will give you an array of `k` uniform random numbers in $[0,1]$. Feel free to read the documentation for the `np.random` submodule if you wish to play around with this, but the precise distribution that you use really won't matter, here.

You should see a noticeable difference (i.e., an order of magnitude or more) as soon as `n` is larger than a few hundred. Crank `n` up to a few hundred thousand or into the millions to see the difference start to really matter!

In [ ]:
# This returns a numpy array of length n
np.random.random(10)

In [ ]:
import time

def eucnorm_time_trial( n ):
    # TODO: code goes here.
    
    # Hint: here's some example code for formatting output.
    # We'll talk more about formatting strings soon.
    #print('Native Python : %f seconds' % slowtime)
    #print('Vectorized numpy : %f seconds' % numpytime)
    pass

In [ ]:
#n=10K should be enough to see an appreciable difference,
# depending on how old you machine is and what other programs are running right now.
eucnorm_time_trial( 10000 )

## Problem 3: broadcasting and matrix-vector operations

Recall from above that when we write something like `np.array([[1,2,3,4]]) + 1`, the operation of adding one is "broadcast" along the vector.
How far can we push this broadcast business? What happens if we try to add an array of length 5 and an array of length 2?

In [ ]:
a = np.array([1,2,3,4,5])
b = np.array([1,2])
a+b

Okay, well maybe the problem is that 2 doesn't divide 5. How about adding a length-2 array and a length-4 array?

In [ ]:
a = np.array([1,2,3,4])
b = np.array([1,2])
a+b

Well, it turns out that the rules for broadcasting in numpy are a bit more complicated... We'll come back to this after a brief detour to talk about higher-order arrays.

Numpy doesn't limit us to vectors-- we saw in lecture that we can create matrices and even higher-order tensors (e.g., a 4-tensor to represent video: 3 dimensions for each of the three color channels and a 4th dimension for time).

Just as we can create a "vector-like" (i.e., one-dimensional) numpy array from a list,
we can create a "matrix-like" numpy array from a list of lists, with each sub-list representing a row of the matrix (all one-dimensional numpy arrays are row vectors by default!):

In [ ]:
M = np.array( [[1,2,3],[4,5,6],[7,8,9]] )
M

Now we have a matrix-like object `M`, with dimension 3-by-3.
Presumably, then, we can use this matrix to multiply a vector.
What should be the result of running the following code?
Make a prediction, then run it.

In [ ]:
M*np.array([2,3,4])

Are you surprised? The issue is that `M` is a numpy array, <i>not a matrix</i>.
Thus, multiplication is entrywise by default.
In particular, numpy broadcasts the entrywise multiplication of each row of `M` with the vector `np.array([2,3,4])` along the rows of `M`.

In [ ]:
# First row of M times the vector
np.array([1,2,3])*np.array([2,3,4])

To make it operate on vectors in the way we would naturally expect, we have to tell numpy to treat `M` like a matrix.
We do that with `np.asmatrix()`, which converts its argument to a numpy `Matrix` object.

In [ ]:
np.asmatrix(M)*np.array([2,3,4])

Hmm... What's the problem here? <b>Discuss!</b>

Okay, yeah, the problem is that by default, all numpy arrays are row vectors, so the code above is trying to multiply a row-vector on the left by a matrix, which usually doesn't work...

On the other hand, this means that the following should work fine:

In [ ]:
np.array([2,3,4])*np.asmatrix(M)

Okay, so how about transposing that vector so we can multiply it on the left?

In [ ]:
np.asmatrix(M)*( np.array([2,3,4]).T  )

Hmm... That's a bit annoying... 

You can drive yourself crazy trying to get these operations to go through correctly (I speak from experience...).

Lucky for us, Python recently added a new binary operator that takes care of all the annoying details for us: rather than having to cast a numpy array to a matrix and all that, we can simply write:

In [ ]:
M @ np.array([2,3,4])

Recall from your linear algebra class that a vector $v$ is an eigenvector of a square matrix $M$ with eigenvalue $\lambda$ if $M v = \lambda v$ (assuming that the matrix-vector product makes sense).

Let's say that a vector $v$ is an $\epsilon$-eigenvector with eigenvalue $\lambda$ if $\| Mv - \lambda v \| \le \epsilon$.

Write a function `approx_evec` that takes four arguments:

- a two-dimensional numpy array `M`
- a one-dimensional numpy array `v`
- a numeric (float or int) `lam`, and
- a numeric (float or int) `epsilon`

and returns `True` if `v` is an `epsilon`-eigenvector of `M` with eigenvalue `lam`, and returns `False` otherwise.
Error checking is entirely optional, and you may assume that `M` and `v` are such that the matrix-vector operation `M @ v` makes sense.



<b>Hint:</b> feel free to use your code written above for computing Euclidean norm, or use the built-in functions in numpy.

In [ ]:
def approx_evec( M, v, lam, epsilon ):
    # If this weren't demo code, we would want to do some error checking here.
    
    # Note: we could also use the built-in numpy functions for computing norms.
    # These are in the numpy.linalg submodule.
    # See https://numpy.org/doc/stable/reference/generated/numpy.linalg.norm.html
    
    pass # TODO: implement actual code instead of the pass statement.

In [ ]:
np.eye(4) # Create an identity matrix

In [ ]:
np.ones(4) # Vector of all ones

In [ ]:
np.zeros(4) # Vector of all zeros.

In [ ]:
approx_evec( 10*np.eye(10), np.ones(10), 1.0, np.sqrt(811.0) ) # Should evaluate to True

In [ ]:
approx_evec( 10*np.eye(10), np.ones(10), 1.0, np.sqrt(809.0) ) # Should evaluate to False

## Problem 4: linear algebra in `scipy`

Roughly speaking, `numpy` handles "basic" numerical operations, while the related `scipy` module handles more "complicated" operations.

As an example of this, the `numpy.linalg` submodule includes a lot of operations for working with matrices, most notably code for computing matrix inverses, eigenvectors and eigenvalues.
`scipy.linalg` is a superset of `numpy.linalg`-- it has more bells and whistles, which you can read about here: https://docs.scipy.org/doc/scipy/tutorial/linalg.html

More importantly, `scipy.linalg` is built using a faster and more efficient set of linear algebraic libraries (read about BLAS/LAPACK if you are interested in these things), so it tends to be faster than the analogous operations in `numpy.linalg`.

Let's use some of `scipy.linalg` to implement our own version of principal components analysis (PCA).

Recall that if we have a data matrix $X \in \mathbb{R}^{n \times p}$ with one data point per row, with singular value decomposition $X = U S V^T$, then PCA maps the $p$-dimensional data (i.e., the rows of $X$) to $k \le p$ dimensions according to the rows of
$$
U_{1:k} S_{1:k},
$$
where $S_{1:k}$ is the diagonal matrix containing the $k$ largest singular values of $X$ and $U_{1:k} \in \mathbb{R}^{n \times k}$ has as its columns the corresponding $k$ left singular vectors.

Use `scipy.linalg.svd` to write a function `my_pca` that takes two arguments: a data matrix `X` (assumed to be a `numpy` array or matrix) and a dimension `k`.
You should include error checking to ensure that `k` is a positive integer and that it is at most equal to the number of columns of `X`.

Documentation for `scipy.linalg.svd` is here: https://docs.scipy.org/doc/scipy/reference/generated/scipy.linalg.svd.html#scipy.linalg.svd

In [ ]:
import scipy.linalg

def my_pca( X, k ):
    # TODO: code goes here.
    pass

In [ ]:
# This hould return a 3-by-2 matrix, whose second column is (0,0,1).
my_pca(np.array([[1,2,0],[2,1,0],[0,0,1]]), 2)